In [1]:
import os
import glob
import warnings
import numpy as np
import xarray as xr

warnings.filterwarnings('ignore')

# Load ensemble predictors from 60 linearly scaled CESM Runs 
files = sorted(glob.glob("/global/cfs/cdirs/m4997/Sagar_ensembles/ncrct_F2000climo_18months_CESM2.2.2_PBNudged_Scaled_*.nc"))

# Multiframe dataset for CESM Runs, 5-Dimensional in: Ensemble, Lat, Lon, Lev, Time
ds = xr.open_mfdataset(files, combine='nested', concat_dim='ensemble')

In [2]:
ds

<xarray.Dataset> Size: 843GB
Dimensions:                  (ensemble: 60, lat: 192, lev: 32, ilev: 33,
                              time: 12, nbnd: 2, lon: 288)
Coordinates:
  * lat                      (lat) float64 2kB -90.0 -89.06 ... 89.06 90.0
  * lon                      (lon) float64 2kB 0.0 1.25 2.5 ... 357.5 358.8
  * lev                      (lev) float64 256B 3.643 7.595 ... 976.3 992.6
  * ilev                     (ilev) float64 264B 2.255 5.032 ... 985.1 1e+03
  * time                     (time) object 96B 2001-02-01 00:00:00 ... 2002-0...
Dimensions without coordinates: ensemble, nbnd
Data variables: (12/545)
    gw                       (ensemble, lat) float64 92kB dask.array<chunksize=(1, 192), meta=np.ndarray>
    hyam                     (ensemble, lev) float64 15kB dask.array<chunksize=(1, 32), meta=np.ndarray>
    hybm                     (ensemble, lev) float64 15kB dask.array<chunksize=(1, 32), meta=np.ndarray>
    P0                       (ensemble) float64 480B 1e+05 1e+05 ... 1e+05 1e+05
    hyai                     (ensemble, ilev) float64 16kB dask.array<chunksize=(1, 33), meta=np.ndarray>
    hybi                     (ensemble, ilev) float64 16kB dask.array<chunksize=(1, 33), meta=np.ndarray>
    ...                       ...
    so4_c3TBF                (ensemble, time, lat, lon) float32 159MB dask.array<chunksize=(1, 12, 192, 288), meta=np.ndarray>
    so4_c3_mixnuc1           (ensemble, time, lat, lon) float32 159MB dask.array<chunksize=(1, 12, 192, 288), meta=np.ndarray>
    so4_c3_sfgaex2           (ensemble, time, lat, lon) float32 159MB dask.array<chunksize=(1, 12, 192, 288), meta=np.ndarray>
    totna500                 (ensemble, time, lev, lat, lon) float32 5GB dask.array<chunksize=(1, 12, 32, 192, 288), meta=np.ndarray>
    wet_deposition_NHx_as_N  (ensemble, time, lat, lon) float32 159MB dask.array<chunksize=(1, 12, 192, 288), meta=np.ndarray>
    wet_deposition_NOy_as_N  (ensemble, time, lat, lon) float32 159MB dask.array<chunksize=(1, 12, 192, 288), meta=np.ndarray>
Attributes:
    Conventions:       CF-1.0
    source:            CAM
    case:              F2000climo_18months_CESM2.2.2_PBNudged_Scaled_0.1
    logname:           srathod
    host:              derecho4
    initial_file:      /glade/campaign/cesm/cesmdata/inputdata/atm/cam/inic/f...
    topography_file:   /glade/campaign/cesm/cesmdata/inputdata/atm/cam/topo/f...
    model_doi_url:     https://doi.org/10.5065/D67H1H0V
    time_period_freq:  month_1
    history:           Thu Jan 30 14:21:54 2025: ncrcat /glade/derecho/scratc...
    NCO:               netCDF Operators version 5.2.4 (Homepage = http://nco....

In [3]:
def extract_features_to_numpy(ds, var_list, valid_mask_path='/global/homes/j/jzweifel/jupyterhub/ML/masks/valid_mask.npy', output_path='X_new_features.npy'):
    """
    Extract one or more CESM variables from a dataset and save them as a standalone numpy array.

    Parameters:
    -----------
    ds : xarray.Dataset
        Dataset containing variables to extract.
    var_list : list of str
        List of variable names in `ds` to add as predictors.
    valid_mask_path : str
        Path to the precomputed valid mask (applies spatial, temporal filtering).
    output_path : str
        Path to save the new numpy array of features (e.g. 'X_new_features.npy').
    """
    import numpy as np
    from dask.diagnostics import ProgressBar

    valid_mask = np.load(valid_mask_path)
    new_features = []

    for var_name in var_list:
        da_var = ds[var_name]
        dims = list(da_var.dims)

        if set(['ensemble', 'time', 'lat', 'lon', 'lev']).issubset(dims):
            # Fully resolved 3D variable
            transpose_order = ['ensemble', 'time', 'lat', 'lon', 'lev']
            last_dim = da_var.sizes['lev']

        elif set(['ensemble', 'time', 'lat', 'lon']).issubset(dims):
            # 2D spatial field, add dummy lev
            da_var = da_var.expand_dims({'lev': [0]})
            transpose_order = ['ensemble', 'time', 'lat', 'lon', 'lev']
            last_dim = 1

        elif set(['ensemble', 'time']).issubset(dims) and 'lat' not in dims and 'lon' not in dims:
            # Timeseries, broadcast to lat/lon + dummy lev
            da_var = da_var.expand_dims({
                'lat': ds['lat'],
                'lon': ds['lon'],
                'lev': [0]
            })
            transpose_order = ['ensemble', 'time', 'lat', 'lon', 'lev']
            last_dim = 1

        else:
            raise ValueError(f"Unsupported variable dimensions for {var_name}: {dims}")

        # Ensure variable matches desired order
        da_transposed = da_var.transpose(*transpose_order)

        # Compute before reshaping (avoid Dask reshape limitations)
        with ProgressBar():
            array_data = da_transposed.data.compute()

        # Reshape and apply mask
        flat_computed = array_data.reshape(-1, last_dim)
        clean_var = flat_computed[valid_mask]
        new_features.append(clean_var)

        print(f"✔️  Extracted {var_name} with shape {clean_var.shape}")

    # Stack new variables horizontally
    new_block = np.concatenate(new_features, axis=1)
    np.save(output_path, new_block)
    print(f"\n✅ Saved extracted features to {output_path}. Final shape: {new_block.shape}")

In [4]:
extract_features_to_numpy(ds, ['CLDLIQ'], output_path='CLDLIQ.npy')

[########################################] | 100% Completed | 254.89 s
✔️  Extracted CLDLIQ with shape (938160, 32)

✅ Saved extracted features to CLDLIQ.npy. Final shape: (938160, 32)
